Inspired from 
https://github.com/fchollet/keras/blob/master/examples/addition_rnn.py

Here I am trying to achive sequence to sequence learning. In this case we are trying to enter 2 numbers as text and add them together but with machine learning.

In [1]:
from keras.models import Sequential
from keras.engine.training import slice_X
from keras.layers import Activation,TimeDistributed,Dense,RepeatVector,recurrent
import numpy as np
from six.moves import range
from keras.utils.visualize_util import plot

Using TensorFlow backend.


In [2]:
class CharacterTable(object):
    def __init__(self,chars):
        self.chars = sorted(set(chars))
        self.char_indices = dict((c,i) for i,c in enumerate(self.chars))
        self.indices_char = dict((i,c) for i,c in enumerate(self.chars))
        
    def enconde(self,C,num_rows):
        X = np.zeros((num_rows,len(self.chars)))
        for i,c in enumerate(C):
            X[i,self.char_indices[c]] = 1
        return X
    
    def decode(self,X,calc_argmax=True):
        if calc_argmax:
            X = X.argmax(axis=-1)
        return ''.join(self.indices_char[x] for x in X)
        
class colors:
    ok = '\033[92m'
    fail = '\033[91m'
    close = '\033[0m'

In [3]:
TRAINING_SIZE = 50000
DIGITS = 3
INVERT = True
MAXLEN = DIGITS + 1 + DIGITS

chars = '0123456789+- '
ctable = CharacterTable(chars)

In [4]:
questions = []
expected = []
seen = set()
print ("Generating...")
count = 1
while len(questions) < TRAINING_SIZE*2:
    if count % 10000 == 0:
        print (count)
        
    f = lambda:int(''.join(np.random.choice(list('0123456789'))
                          for i in range(np.random.randint(1,DIGITS+1))))
    a , b = f(), f()
    
    key = tuple(sorted((a,b)))
    if key in seen:
        continue
    seen.add(key)
    
    q1 = '{}+{}'.format(a,b)
    q2 = '{}-{}'.format(a,b)
    query1 = q1 + ' '*(MAXLEN-len(q1))
    query2 = q2 + ' '*(MAXLEN-len(q2))
    ans1 = str(a+b)
    ans1 +=' '*(DIGITS+1-len(ans1))
    ans2 = str(a-b)
    ans2 +=' '*(DIGITS+1-len(ans2))
    
    #if INVERT:
        #query = query[::-1]
    questions.append(query1)
    expected.append(ans1)
    questions.append(query2)
    expected.append(ans2)
    count += 1
    
    
print ("Total addition questions = {}".format(len(questions)))

    

Generating...
10000
20000
20000
20000
30000
30000
30000
40000
40000
40000
40000
40000
40000
40000
40000
40000
40000
50000
50000
50000
50000
50000
Total addition questions = 100000


In [5]:
# Remember the questions are inverted
print ('Few examples of input and output :')
for i in range(6):
    print ("{} = {}".format(questions[i],expected[i]))


Few examples of input and output :
21+272  = 293 
21-272  = -251
36+1    = 37  
36-1    = 35  
15+1    = 16  
15-1    = 14  


In [6]:
print ('Vecotrization...')
X = np.zeros((len(questions),MAXLEN,len(chars)),dtype=np.bool)
y = np.zeros((len(questions),DIGITS+1,len(chars)),dtype=np.bool)
for i, sentence in enumerate(questions):
    X[i] = ctable.enconde(sentence,MAXLEN)

for i, sentence in enumerate(expected):
    y[i] = ctable.enconde(sentence,DIGITS+1)
    


Vecotrization...


In [7]:
#Randomizing the input and output
indices = np.arange(len(y))
np.random.shuffle(indices)
X = X[indices]
y = y[indices]

In [8]:
# Separating 10% of the data for test and 90% data for training.
split_at = len(X) - len(X)//10
(X_train, X_test) = (slice_X(X,0,split_at),slice_X(X,split_at))
(y_train, y_test) = (y[:split_at],y[split_at:])

print ("Training Data :")
print (X_train.shape)
print (y_train.shape)

print ("Test Data :")
print (X_test.shape)
print (y_test.shape)

Training Data :
(90000, 7, 13)
(90000, 4, 13)
Test Data :
(10000, 7, 13)
(10000, 4, 13)


In [9]:
RNN = recurrent.LSTM
HIDDEN_SIZE = 128
BATCH_SIZE = 128
LAYERS = 1

In [10]:
model = Sequential()
model.add(RNN(HIDDEN_SIZE,input_shape=(MAXLEN,len(chars))))
model.add(RepeatVector(DIGITS+1))

for _ in range(LAYERS):
    model.add(RNN(HIDDEN_SIZE,return_sequences=True))
    
model.add(TimeDistributed(Dense(len(chars))))
model.add(Activation('softmax'))
model.compile(loss = 'categorical_crossentropy',
             optimizer='adam', metrics=['accuracy'])

In [ ]:
model.summary()

____________________________________________________________________________________________________
Layer (type)                     Output Shape          Param #     Connected to                     
lstm_1 (LSTM)                    (None, 128)           72704       lstm_input_1[0][0]               
____________________________________________________________________________________________________
repeatvector_1 (RepeatVector)    (None, 4, 128)        0           lstm_1[0][0]                     
____________________________________________________________________________________________________
lstm_2 (LSTM)                    (None, 4, 128)        131584      repeatvector_1[0][0]             
____________________________________________________________________________________________________
timedistributed_1 (TimeDistribut (None, 4, 13)         1677        lstm_2[0][0]                     
___________________________________________________________________________________________

In [ ]:
for iteration in range(1,100):
    print ()
    print ('-'*50)
    print ('Iteration - ',iteration)
    model.fit(X_train,y_train,batch_size=BATCH_SIZE,nb_epoch=1,validation_data=(X_test,y_test))
    
    for i in range(2):
        ind = np.random.randint(0,len(X_test))
        rowX, rowy = X_test[np.array([ind])], y_test[np.array([ind])]
        preds = model.predict_classes(rowX,verbose=0)
        q = ctable.decode(rowX[0])
        correct = ctable.decode(rowy[0])
        guess = ctable.decode(preds[0],calc_argmax=False)
        
        print (" Q ", q[::-1] if INVERT else q)
        print (" T ", correct)
        if correct == guess:
            print (colors.ok +'☑' + colors.close,end = " ")
        else:
            print (colors.fail + '☒' + colors.close,end = " ")
            
        print (guess)
        print ('---')
                
    


--------------------------------------------------
Iteration -  1
Train on 90000 samples, validate on 10000 samples
Epoch 1/1
90000/90000 [==============================] - 75s - loss: 1.8017 - acc: 0.3513 - val_loss: 1.6675 - val_acc: 0.3886

In [12]:
plot(model,to_file='model.png',show_shapes=True)